# Description of the problem

This capstone project will be graded by your peers. This capstone project is worth 70% of your total grade. The project will be completed over the course of 2 weeks.  Week 1 submissions will be worth 30% whereas week 2 submissions will be worth 40% of your total grade.

1 / For this week, you will required to submit the following:

A description of the problem and a discussion of the background. (15 marks)
A description of the data and how it will be used to solve the problem. (15 marks)

2 / For the second week, the final deliverables of the project will be:

A link to your Notebook on your Github repository, showing your code. (15 marks)
A full report consisting of all of the following components (15 marks):

    Introduction where you discuss the business problem and who would be interested in this project.

    Data where you describe the data that will be used to solve the problem and the source of the data.

    Methodology section which represents the main component of the report where you discuss and describe any exploratory data analysis that you did, any inferential statistical testing that you performed, if any, and what machine learnings were used and why.

    Results section where you discuss the results.

    Discussion section where you discuss any observations you noted and any recommendations you can make based on the results.

    Conclusion section where you conclude the report.

3 / Your choice of a presentation or blogpost. (10 marks)

# Introduction where you discuss the business problem and who would be interested in this project.

Paris and its suburbs are managed by a company called RATP for transports. We will analyse the stations from the RATP open data website and try to understand how it works trough geolocalisation data. The goal is to find geolocalised points that may suit the opening of a business based on public transport availability.

    1/ We will get the food data from foursquare API and see how many food venues there is for each station as an example and plot it in folium

    2/ We will use a clustering algorithm to understand the best positions that are accessible trough public transport ( of RATP ) based on their data

Anyone willing to invest in a new house or any new business that wishes to be accessible by public transports will find this analysis useful.

The data is accessible at this link https://data.ratp.fr/explore/dataset/positions-geographiques-des-stations-du-reseau-ratp/information/?disjunctive.stop_name . It is from RATP which is representing France main region transport system , it is part of the open data, which is free and accessible.

The data by itself has a latitude and longitude + name and adress of the stations.

    - Latitude and longitude will be used to get specific locations and plot it on a map with folium 
    
    - Latitude and longitude will be used to get information from foursquare API.
    
In all cases the data needs to be transformed to be used in terms of analysis. The data set will anyway be reduced and filtered to avoid duplicates, it may be simplified as well to be able to fit the number of maximum calls per day we have with the foursquare API. 

### Methodology section which represents the main component of the report where you discuss and describe any exploratory data analysis that you did, any inferential statistical testing that you performed, if any, and what machine learnings were used and why.

In [1]:
import requests # library to handle requests
import pandas as pd # library for data analsysis
import numpy as np # library to handle data in a vectorized manner
import random # library for random number generation


!pip install geopy
from geopy.geocoders import Nominatim # module to convert an address into latitude and longitude values

# libraries for displaying images
from IPython.display import Image 
from IPython.core.display import HTML 
    
# tranforming json file into a pandas dataframe library
from pandas.io.json import json_normalize


! pip install folium==0.5.0
import folium # plotting library

print('Folium installed')
print('Libraries imported.')

Folium installed
Libraries imported.


# 1. A description of the data and how it will be used to solve the problem.

In [2]:
# The code was removed by Watson Studio for sharing.

ID                               Name  \
0  7275123                   GERARD DE NERVAL   
1  7275132                            SIMPLON   
2  7275139  MAGENTA - MAUBEUGE - GARE DU NORD   
3  7275143                      GARE DE L'EST   
4  7275158                      AUGUSTE COMTE   

                                Description                  Coordinates  dist  
0  AVENUE DE LA PORTE DE MONTMARTRE - 75118  48.9007204012,2.33519629626   NaN  
1               46 BOULEVARD ORNANO - 75118  48.8948064764,2.34715016514   NaN  
2      140-142 BOULEVARD DE MAGENTA - 75110  48.8813341943,2.35171250385   NaN  
3        74 BOULEVARD DE STRASBOURG - 75110  48.8755903947,2.35801931852   NaN  
4         68 BOULEVARD SAINT-MICHEL - 75106   48.844145249,2.33887508382   NaN

In [3]:

body = client_8785d818e39141bfab835644b9aef929.get_object(Bucket='projectcoursera-donotdelete-pr-hhhvu4vaoaiaew',Key='positions-geographiques-des-stations-du-reseau-ratp (1).csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

raw_data_complete = pd.read_csv(body, sep=";")
raw_data_complete.head()


ID               Name                            Description  \
0  3677677    RUE DE LA FERME  ROND-POINT MARTIN LUTHER KING - 77258   
1  3677688  COLLEGE LE LUZARD               COURS DES ROCHES - 77337   
2  3678812     ZONE TECHNIQUE        ROUTE DES ANNIVERSAIRES - 95527   
3  3678816     ENTRETIEN NORD           ROUTE DE L'ARPENTEUR - 95527   
4  3682876              AVRON   63 BOULEVARD ALSACE-LORRAINE - 94058   

                   Coordinates  
0  48.8359484574,2.62990289517  
1     48.8467902961,2.61369101  
2   49.0119496186,2.5332905562  
3  49.0114652199,2.51552950645  
4  48.8500655011,2.49939528589

### Data transformation

In [4]:
#Splitting the coordinates column into two 
raw_data_complete.Coordinates.str.split(',',expand=True)

0              1
0      48.8359484574  2.62990289517
1      48.8467902961     2.61369101
2      49.0119496186   2.5332905562
3      49.0114652199  2.51552950645
4      48.8500655011  2.49939528589
...              ...            ...
25333  48.9033027924  2.19339213468
25334  48.8891783882  2.23088294789
25335  48.7882424652  2.29326524827
25336  48.7857019409  2.30251642637
25337  48.7797434214  2.28046129207

[25338 rows x 2 columns]

In [5]:
# Merging the new dataframe
coordinate = raw_data_complete["Coordinates"].str.split(",", expand = True) 
coordinate.columns = ['Latitude', 'Longitude']
frames = [raw_data_complete, coordinate]

#result = pd.concat(frames, ignore_index=False)
result = raw_data_complete.join(coordinate)

result

ID                    Name                            Description  \
0      3677677         RUE DE LA FERME  ROND-POINT MARTIN LUTHER KING - 77258   
1      3677688       COLLEGE LE LUZARD               COURS DES ROCHES - 77337   
2      3678812          ZONE TECHNIQUE        ROUTE DES ANNIVERSAIRES - 95527   
3      3678816          ENTRETIEN NORD           ROUTE DE L'ARPENTEUR - 95527   
4      3682876                   AVRON   63 BOULEVARD ALSACE-LORRAINE - 94058   
...        ...                     ...                                    ...   
25333  4024335  BOULEVARD DE LA SEINE.                       R KLEBER - 92050   
25334  4024351  BERTHELOT - CARRE VERT  FACE 16 R MARCELLIN BERTHELOT - 92062   
25335  3909108  FONTENAY-AUX-ROSES RER              25 AVENUE LOMBART - 92032   
25336  3909111              LES BLAGIS   FACE 119 AVENUE GABRIEL PERI - 92032   
25337  3909833            ROBINSON RER           FACE 3 AV DU PLESSIS - 92071   

                       Coordinates       Latitude      Longitude  
0      48.8359484574,2.62990289517  48.8359484574  2.62990289517  
1         48.8467902961,2.61369101  48.8467902961     2.61369101  
2       49.0119496186,2.5332905562  49.0119496186   2.5332905562  
3      49.0114652199,2.51552950645  49.0114652199  2.51552950645  
4      48.8500655011,2.49939528589  48.8500655011  2.49939528589  
...                            ...            ...            ...  
25333  48.9033027924,2.19339213468  48.9033027924  2.19339213468  
25334  48.8891783882,2.23088294789  48.8891783882  2.23088294789  
25335  48.7882424652,2.29326524827  48.7882424652  2.29326524827  
25336  48.7857019409,2.30251642637  48.7857019409  2.30251642637  
25337  48.7797434214,2.28046129207  48.7797434214  2.28046129207  

[25338 rows x 6 columns]

In [6]:
#result['Latitude'].astype('float64')
#result['Longitude'].astype('float64')
result["Latitude"] = pd.to_numeric(result["Latitude"])
result["Longitude"] = pd.to_numeric(result["Longitude"])
result['Name']= result['Name'].astype(str)
result.Name = result.Name.astype(str)

In [7]:
result.dtypes

ID               int64
Name            object
Description     object
Coordinates     object
Latitude       float64
Longitude      float64
dtype: object

In [8]:
#drop duplicated
result.drop_duplicates(subset =("Name","Description"), keep = False, inplace = True)
#Moving from 25338 rows × 6 columns  to 4790 rows × 6 columns

In [9]:
address = 'paris'
geolocator = Nominatim(user_agent="paris_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Paris are {}, {}.'.format(latitude, longitude))



The geograpical coordinate of Paris are 48.8566969, 2.3514616.


In [10]:
map_of_paris = folium.Map(location=[48.8, 2.35], zoom_start=12)


In [12]:
sum_markers =0
# add markers to map
for lat, lng, name in zip(result['Latitude'], result['Longitude'], result['Name']):
    #print(str(lng) +' '+ str(lat) + ' '  +str(name))
    label = ' {}'.format(name)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=0.3,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=True).add_to(map_of_paris)
    
    sum_markers = sum_markers + 1 
    print(sum_markers)

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


In [13]:
print(sum_markers)

4790


In [14]:
map_of_paris

### FOURSQUARE API INTEGRATION

In [51]:
# The code was removed by Watson Studio for sharing.

We will use Foursquare API to explore venue categories surrounding each station. Venues can be categorized as residential, professional, shopping or leisure. Let's see what venue categories Foursquare identifies.



In [54]:
categories_url = 'https://api.foursquare.com/v2/venues/categories?client_id={}&client_secret={}&v={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION)
            
# make the GET request
results = requests.get(categories_url).json()
print(results)

{'meta': {'code': 429, 'errorType': 'quota_exceeded', 'errorDetail': 'Quota exceeded', 'requestId': '5ffd8526ba07166a6a8a069c'}, 'response': {}}


In [53]:
len(results['response']['categories'])

KeyError: 'categories'

There are 10 top-level categories and multiple subcategories

Let's print only the top-level categories and their IDs and also add them to categories_list



In [47]:
categories_list = []
# Let's print only the top-level categories and their IDs and also add them to categories_list

def print_categories(categories, level=0, max_level=0):    
    if level>max_level: return
    out = ''
    out += '-'*level
    for category in categories:
        print(out + category['name'] + ' (' + category['id'] + ')')
        print_categories(category['categories'], level+1, max_level)
        categories_list.append((category['name'], category['id']))
        
print_categories(results_request['response']['categories'], 0, 0)

KeyError: 'categories'

### Methodology

We will use the foursquare API to understand food related venues. It will simplify the numbers of request to the foursquare API, since we have lots of data. We will also remove duplicates based on the name of the station, we previously removed the duplicates on name and description.



In [48]:

result_name_duplicate = result
#result.drop_duplicates(subset =("Name"), keep = False)
result_name_duplicate.shape

(4790, 6)

### USING FOURSQUARE API

In [55]:
def get_food_count(ll, radius, categoryId):
    explore_url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={}&radius={}&categoryId={}'.format(
                CLIENT_ID, 
                CLIENT_SECRET, 
                VERSION,
                ll,
                radius,
                categoryId)

    # make the GET request
    return requests.get(explore_url).json()['response']['totalResults']

print(get_food_count('48.8359484574,2.62990289517',300,'4d4b7105d754a06374d81259'))

KeyError: 'totalResults'

In [56]:
#Create new dataframe to store food venues data
stations_venues_df = result_name_duplicate.copy()
stations_venues_df.shape


(4790, 6)

In [57]:
stations_venues_df.head()

ID          Name                          Description  \
8   3682980   DISPENSAIRE    FACE 39 RUE DE LA LIBERTE - 77108   
22  3685930      VEDRINES       54 AVENUE ERNEST RENAN - 94033   
23  3685931  ERNEST RENAN  172-174 AVENUE ERNEST RENAN - 93048   
24  3685974      VEDRINES       23 AVENUE ERNEST RENAN - 93048   
63  7311988  LES PLATANES             ALL DES PLATANES - 77146   

                    Coordinates   Latitude  Longitude  
8   48.8767496173,2.59993914757  48.876750   2.599939  
22  48.8560696327,2.46161860012  48.856070   2.461619  
23  48.8565224898,2.46678170321  48.856522   2.466782  
24   48.8561601595,2.4609922971  48.856160   2.460992  
63  48.8298147009,2.64923984584  48.829815   2.649240

In [ ]:
#Request number of venues, store result as CSV
for i, row in stations_venues_df.iterrows():
    print(i)
    print(row)
    stations_venues_df.loc[i, 'Food Venues'] = get_food_count(stations_venues_df.Coordinates.iloc[i], radius=150, categoryId='4d4b7105d754a06374d81259')
    stations_venues_df.to_csv('stations_venues.csv')

In [ ]:
df_food_counts = pd.read_csv('stations_venues.csv',index_col=0)
df_food_counts.head()


In [ ]:
map_of_paris_food_size = folium.Map(location=[48.8, 2.35], zoom_start=8)


In [ ]:
#Map based on the value of the food venues to understand areas where the food venues are higher
sum_markers =0
# add markers to map
for lat, lng, name, value in zip(df_food_counts['Latitude'], df_food_counts['Longitude'], df_food_counts['Description'], df_food_counts['Food Venues']):
    label = ' {}'.format(name)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=value*2,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=True).add_to(map_of_paris_food_size)
    
    sum_markers = sum_markers + 1 
    print(sum_markers / len(locationlist) )

In [ ]:
map_of_paris_food_size